In [11]:
!python settings.py

Using device: cuda


In [12]:
import os
import numpy as np
import pandas as pd
from tqdm.autonotebook import tqdm

import faiss
from sentence_transformers import SentenceTransformer, CrossEncoder

from settings import OUTPUT_DIR, DEVICE

os.environ['WANDB_DISABLED'] = 'true'

from transformers import logging
logging.set_verbosity_error()

In [13]:
# data = {
#     'corpus': pd.read_parquet('data/processed/corpus_data.parquet'),
#     'train' : pd.read_parquet('data/processed/train_data.parquet'),
#     'test'  : pd.read_parquet('data/processed/test_data.parquet')
# }
# for split in ['train', 'test']:
#     data[split]['cid']          = data[split]['cid'].apply(lambda x: x.tolist())
#     data[split]['context_list'] = data[split]['context_list'].apply(lambda x: x.tolist())

In [14]:
fine_tuned_model = SentenceTransformer(OUTPUT_DIR, device=DEVICE)
fine_tuned_model.half()

SentenceTransformer(
  (0): Transformer({'max_seq_length': 512, 'do_lower_case': False}) with Transformer model: BertModel 
  (1): Pooling({'word_embedding_dimension': 768, 'pooling_mode_cls_token': False, 'pooling_mode_mean_tokens': True, 'pooling_mode_max_tokens': False, 'pooling_mode_mean_sqrt_len_tokens': False, 'pooling_mode_weightedmean_tokens': False, 'pooling_mode_lasttoken': False, 'include_prompt': True})
)

In [15]:
passages          = pd.read_parquet('data/processed/corpus_data.parquet')['text'].tolist()
# corpus_embeddings = fine_tuned_model.encode(
#     passages, 
#     batch_size=128,
#     convert_to_numpy=True, 
#     normalize_embeddings=True,
#     show_progress_bar=True, 
#     device=DEVICE,
# ).astype(np.float32)

In [16]:
# d         = corpus_embeddings.shape[1]  # 768
# cpu_index = faiss.IndexFlatIP(d)

# res       = faiss.StandardGpuResources()
# gpu_index = faiss.index_cpu_to_gpu(res, 0, cpu_index)
# gpu_index.add(corpus_embeddings)

In [17]:
# final_cpu_index = faiss.index_gpu_to_cpu(gpu_index)
# faiss.write_index(final_cpu_index, 'data/retrieval/legal_faiss.index')

In [18]:
legal_index = faiss.read_index('data/retrieval/legal_faiss.index')

In [19]:
def retrieval(emb_model, query, index, top_k=10):
    q_emb = emb_model.encode(
        query, 
        convert_to_numpy=True, 
        normalize_embeddings=True,
    ).astype(np.float32).reshape(1, -1)
    
    scores, indices = index.search(q_emb, top_k)  # shape: (1, top_k)
    
    cand_idxs   = indices[0]
    cand_scores = scores[0]
    cand_texts  = [passages[i] for i in cand_idxs]

    results = [{
        'index': int(cand_idxs[i]),
        'score': float(cand_scores[i]),
        'text': cand_texts[i]
    } for i in range(len(cand_idxs))]
    
    return results

In [22]:
query = 'Tội xúc phạm danh dự'
hits  = retrieval(fine_tuned_model, query, legal_index, top_k=10)

for h in hits:
    print(f"[Rank {hits.index(h)+1}] index={h['index']}, score={h['score']:.4f}")
    print(f"{h['text']}\n{'-'*80}")

[Rank 1] index=76423, score=0.6417
Tội làm nhục người khác
1. Người nào xúc phạm nghiêm trọng nhân phẩm, danh dự của người khác, thì bị phạt cảnh cáo, phạt tiền từ 10.000.000 đồng đến 30.000.000 đồng hoặc phạt cải tạo không giam giữ đến 03 năm.
...
--------------------------------------------------------------------------------
[Rank 2] index=99131, score=0.6155
“Người nào có hành vi xâm phạm danh dự, nhân phẩm của người khác mà gây thiệt hại thì phải bồi thường.”
--------------------------------------------------------------------------------
[Rank 3] index=228550, score=0.5932
i) Điều 353, các khoản 2, 3 và 4 (tội tham ô tài sản); Điều 354, các khoản 2, 3 và 4 (tội nhận hối lộ); Điều 355, các khoản 2, 3 và 4 (tội lạm dụng chức vụ, quyền hạn chiếm đoạt tài sản); Điều 356, các khoản 2 và 3 (tội lợi dụng chức vụ, quyền hạn trong khi thi hành công vụ); Điều 357, các khoản 2 và 3 (tội lạm quyền trong khi thi hành công vụ); Điều 358, các khoản 2, 3 và 4 (tội lợi dụng chức vụ, quyền hạn gây

In [ ]:
# def search(model, query, index, k=10):
#     query_embedding = model.encode(
#         query, 
#         convert_to_numpy=True, 
#         normalize_embeddings=True,
#     ).astype(np.float32).reshape(1, -1)

#     scores, indices = index.search(query_embedding, k*3)
#     hits = [{'score': scores[0][i], 'index': indices[0][i]} for i in range(len(scores[0]))]
#     return hits

In [ ]:
# hits = search(
#     model=fine_tuned_model, 
#     query='Hợp đồng lao động là gì?', 
#     index=legal_index, 
#     k=10
# )

# for rank, hit in enumerate(hits):
#     print(f"[Rank: {rank + 1}]")
#     print(f"(Index: {hit['index']}Score: {hit['score']:.4f})\n")
#     print(passages[hit['index']])
#     print('-' * 100)
#     print()